In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import tensorflow.keras as tf
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.callbacks import EarlyStopping
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler , FunctionTransformer
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import SimpleRNN, Dense, LSTM , Dropout
from tensorflow.keras.optimizers import Adam
import deflatebr as dbr
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer

In [3]:
df  = pd.read_csv("../raw_data/all_urban_expanded_ML.csv")

In [4]:
df.head()

Ano  Código_IBGE  Aprovação  Reprovação  Abandono  Matrículas  Docentes  \
0  2012      1100023       69.9        16.6      13.5        3453       172   
1  2012      1100031       91.3         5.2       3.5         230        22   
2  2012      1100064       86.9         5.6       7.5         733        54   
3  2012      1100072       83.3         4.4      12.3         237        19   
4  2012      1100080       78.0         4.9      17.1         380        28   

   Estabelecimentos  Turmas          PIB  Poverty_%  Unemployed_%  \
0                 6     136  18938.68679      31.61          6.35   
1                 1      11  18938.68679      31.61          6.35   
2                 3      32  18938.68679      31.61          6.35   
3                 1      13  18938.68679      31.61          6.35   
4                 1      14  18938.68679      31.61          6.35   

   Acesso_a_internet_%  Adjusted_population  Adjusted_funding  
0                   21             78834.95      3.019012e+07  
1                   21              5212.20      1.293170e+06  
2                   21             15379.05      2.392587e+06  
3                   21              7250.50      1.941973e+06  
4                   21             12201.75      4.469983e+06

In [5]:
df.dtypes

Ano                      int64
Código_IBGE              int64
Aprovação              float64
Reprovação             float64
Abandono               float64
Matrículas               int64
Docentes                 int64
Estabelecimentos         int64
Turmas                   int64
PIB                    float64
Poverty_%              float64
Unemployed_%           float64
Acesso_a_internet_%      int64
Adjusted_population    float64
Adjusted_funding       float64
dtype: object

In [6]:
def transform_column(df: pd.DataFrame, column_name):
    if column_name not in df.columns:
      raise ValueError(f"A coluna '{column_name}' não existe no DataFrame.")

    # Converter
    df[column_name] = df[column_name].astype(str)

    # Adiciona "-01"
    df[column_name] = df[column_name] + "-01"

    return df
    
df_urban  = transform_column(df, 'Ano')

In [7]:
def deflate_adjusted_funding(df: pd.DataFrame, date_column_name, funding_column_name):
    years = df[date_column_name].unique()

    for year in years:
        df_year = df[df[date_column_name] == year]
        df_d = dbr.deflate(nominal_values=df_year[funding_column_name], nominal_dates=df_year[date_column_name], real_date='2020-01')
        df.loc[df[date_column_name] == year, funding_column_name] = df_d

    # Remove "-01" from the date values and convert them to integers
    df[date_column_name] = df[date_column_name].str.replace('-01', '').astype(int)

    return df

# Using
df_urban_transformed = deflate_adjusted_funding(df_urban, 'Ano', 'Adjusted_funding')

In [8]:
df_urban_transformed.head()

Ano  Código_IBGE  Aprovação  Reprovação  Abandono  Matrículas  Docentes  \
0  2012      1100023       69.9        16.6      13.5        3453       172   
1  2012      1100031       91.3         5.2       3.5         230        22   
2  2012      1100064       86.9         5.6       7.5         733        54   
3  2012      1100072       83.3         4.4      12.3         237        19   
4  2012      1100080       78.0         4.9      17.1         380        28   

   Estabelecimentos  Turmas          PIB  Poverty_%  Unemployed_%  \
0                 6     136  18938.68679      31.61          6.35   
1                 1      11  18938.68679      31.61          6.35   
2                 3      32  18938.68679      31.61          6.35   
3                 1      13  18938.68679      31.61          6.35   
4                 1      14  18938.68679      31.61          6.35   

   Acesso_a_internet_%  Adjusted_population  Adjusted_funding  
0                   21             78834.95      4.728818e+07  
1                   21              5212.20      2.025552e+06  
2                   21             15379.05      3.747620e+06  
3                   21              7250.50      3.041802e+06  
4                   21             12201.75      7.001541e+06

In [9]:
import pandas as pd

def encode_and_convert_to_int(df: pd.DataFrame, column_name):
   
    encoded_df = pd.get_dummies(df, columns=[column_name])
    
    # Convert to int
    colunas_codigo_ibge = encoded_df.columns[encoded_df.columns.str.startswith('Código_IBGE_')].tolist()
    
    # Converter as colunas para int32 no DataFrame original
    df[colunas_codigo_ibge] = encoded_df[colunas_codigo_ibge].astype(int)
    
    # Drop da coluna original 'Código_IBGE'
    df.drop(column_name, axis=1, inplace=True)
    
    return df
    
# Using
df_urban_encoded = encode_and_convert_to_int(df_urban_transformed, 'Código_IBGE')

/var/folders/3b/gl16xrd93txb9yh4g5v099740000gn/T/ipykernel_36128/3437952031.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[colunas_codigo_ibge] = encoded_df[colunas_codigo_ibge].astype(int)
/var/folders/3b/gl16xrd93txb9yh4g5v099740000gn/T/ipykernel_36128/3437952031.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[colunas_codigo_ibge] = encoded_df[colunas_codigo_ibge].astype(int)
/var/folders/3b/gl16xrd93txb9yh4g5v099740000gn/T/ipykernel_36128/3437952031.py:11: PerformanceWarning: DataFrame is highly fragmented.  

In [10]:
def split_data(df, target_column):
    features = df.drop(target_column, axis=1)
    targets = df[target_column]

    X_train, X_test, y_train, y_test = train_test_split(features, targets, test_size=0.2, random_state=42)

    return X_train, X_test, y_train, y_test

# Using
X_train, X_test, y_train, y_test = split_data(df_urban_encoded, 'Adjusted_funding')

In [11]:
import numpy as np
from sklearn.preprocessing import MinMaxScaler

def scale_features(features):
    scaler = MinMaxScaler()
    scaled_features = scaler.fit_transform(features)
    return scaled_features

# Using
scaled_X_train = scale_features(X_train)
scaled_X_test = scale_features(X_test)

In [12]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error

 
# create regressor object
model = RandomForestRegressor(n_estimators=100,
                                  random_state=42)
 
# fit
model.fit(scaled_X_train, y_train)

# Use the trained model
y_pred = model.predict(scaled_X_test)

# Calculate the Mean Absolute Error (MAE)
mae = mean_absolute_error(y_test, y_pred)

print("Mean Absolute Error:", mae)

Mean Absolute Error: 1913223.1798706197


In [ ]:
#from sklearn.ensemble import RandomForestRegressor
#from sklearn.model_selection import GridSearchCV

# model
#base_model = RandomForestRegressor(n_estimators=100, random_state=42)

# Passo 3: Crie um dicionário de hiperparâmetros
#param_grid = {
   # 'n_estimators': [100, 200, 300],
  #  'max_depth': [None, 10, 20, 30],
   # 'min_samples_split': [2, 5, 10],
   # 'min_samples_leaf': [1, 2, 4]
#}

# Passo 4: Crie o objeto GridSearchCV
#grid_search = GridSearchCV(estimator=base_model, param_grid=param_grid, scoring='neg_mean_absolute_error', cv=5, n_jobs=-1)

# Passo 5: Ajuste o Grid Search aos seus dados
#grid_search.fit(scaled_X_train, y_train)

# Passo 6: Obtenha os melhores hiperparâmetros
#best_params = grid_search.best_params_
#print("Melhores hiperparâmetros:", best_params)

# Passo 7: Avalie o modelo com os melhores hiperparâmetros
#best_model = grid_search.best_estimator_

In [45]:
df2  = pd.read_csv("../raw_data/all_urban_expanded_ML.csv")

In [35]:
# filtered_dataframe = df2[(df2['Ano'] == 2020) & (df2['Código_IBGE'] == 1100023)]
# filtered_dataframe


Ano  Código_IBGE  Aprovação  Reprovação  Abandono  Matrículas  \
44298  2020      1100023       94.4         4.3       1.3        2958   

       Docentes  Estabelecimentos  Turmas       PIB  Poverty_%  Unemployed_%  \
44298       179                 6     115  28722.45       19.7        10.425   

       Acesso_a_internet_%  Adjusted_population  Adjusted_funding  
44298                   81             93094.55       43640824.02

In [46]:
encode_and_convert_to_int(df2, 'Código_IBGE')

/var/folders/3b/gl16xrd93txb9yh4g5v099740000gn/T/ipykernel_36128/3437952031.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[colunas_codigo_ibge] = encoded_df[colunas_codigo_ibge].astype(int)
/var/folders/3b/gl16xrd93txb9yh4g5v099740000gn/T/ipykernel_36128/3437952031.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[colunas_codigo_ibge] = encoded_df[colunas_codigo_ibge].astype(int)
/var/folders/3b/gl16xrd93txb9yh4g5v099740000gn/T/ipykernel_36128/3437952031.py:11: PerformanceWarning: DataFrame is highly fragmented.  

Ano  Aprovação  Reprovação  Abandono  Matrículas  Docentes  \
0      2012       69.9        16.6      13.5        3453       172   
1      2012       91.3         5.2       3.5         230        22   
2      2012       86.9         5.6       7.5         733        54   
3      2012       83.3         4.4      12.3         237        19   
4      2012       78.0         4.9      17.1         380        28   
...     ...        ...         ...       ...         ...       ...   
49831  2020       93.0         5.9       1.1        5069       276   
49832  2020      100.0         0.0       0.0         125        12   
49833  2020       97.2         2.6       0.2         496        23   
49834  2020       99.2         0.8       0.0         362        18   
49835  2020      100.0         0.0       0.0         229        11   

       Estabelecimentos  Turmas          PIB  Poverty_%  ...  \
0                     6     136  18938.68679      31.61  ...   
1                     1      11  18938.68679      31.61  ...   
2                     3      32  18938.68679      31.61  ...   
3                     1      13  18938.68679      31.61  ...   
4                     1      14  18938.68679      31.61  ...   
...                 ...     ...          ...        ...  ...   
49831                12     161  31506.97000      18.05  ...   
49832                 1       6  31506.97000      18.05  ...   
49833                 1      19  31506.97000      18.05  ...   
49834                 1      15  31506.97000      18.05  ...   
49835                 1       9  31506.97000      18.05  ...   

       Código_IBGE_5221601  Código_IBGE_5221700  Código_IBGE_5221809  \
0                        0                    0                    0   
1                        0                    0                    0   
2                        0                    0                    0   
3                        0                    0                    0   
4                        0                    0                    0   
...                    ...                  ...                  ...   
49831                    0                    0                    0   
49832                    0                    0                    0   
49833                    0                    0                    0   
49834                    0                    0                    0   
49835                    0                    0                    0   

       Código_IBGE_5221858  Código_IBGE_5221908  Código_IBGE_5222005  \
0                        0                    0                    0   
1                        0                    0                    0   
2                        0                    0                    0   
3                        0                    0                    0   
4                        0                    0                    0   
...                    ...                  ...                  ...   
49831                    1                    0                    0   
49832                    0                    1                    0   
49833                    0                    0                    1   
49834                    0                    0                    0   
49835                    0                    0                    0   

       Código_IBGE_5222054  Código_IBGE_5222203  Código_IBGE_5222302  \
0                        0                    0                    0   
1                        0                    0                    0   
2                        0                    0                    0   
3                        0                    0                    0   
4                        0                    0                    0   
...                    ...                  ...                  ...   
49831                    0                    0                    0   
49832                    0                    0                    0   
49833               

In [47]:
ultima_linha_df = pd.DataFrame(df2.iloc[-1]).transpose()

# Agora, 'ultima_linha_df' é um DataFrame que contém a última linha do seu DataFrame 'df'
ultima_linha_df

Ano  Aprovação  Reprovação  Abandono  Matrículas  Docentes  \
49835  2020.0      100.0         0.0       0.0       229.0      11.0   

       Estabelecimentos  Turmas       PIB  Poverty_%  ...  \
49835               1.0     9.0  31506.97      18.05  ...   

       Código_IBGE_5221601  Código_IBGE_5221700  Código_IBGE_5221809  \
49835                  0.0                  0.0                  0.0   

       Código_IBGE_5221858  Código_IBGE_5221908  Código_IBGE_5222005  \
49835                  0.0                  0.0                  0.0   

       Código_IBGE_5222054  Código_IBGE_5222203  Código_IBGE_5222302  \
49835                  0.0                  1.0                  0.0   

       Código_IBGE_5300108  
49835                  0.0  

[1 rows x 5283 columns]

In [48]:
ultima_linha_df['Adjusted_funding']

49835    3792370.259
Name: Adjusted_funding, dtype: float64

In [49]:
X_new_encoded = ultima_linha_df

In [50]:
X_new_encoded.head()

Ano  Aprovação  Reprovação  Abandono  Matrículas  Docentes  \
49835  2020.0      100.0         0.0       0.0       229.0      11.0   

       Estabelecimentos  Turmas       PIB  Poverty_%  ...  \
49835               1.0     9.0  31506.97      18.05  ...   

       Código_IBGE_5221601  Código_IBGE_5221700  Código_IBGE_5221809  \
49835                  0.0                  0.0                  0.0   

       Código_IBGE_5221858  Código_IBGE_5221908  Código_IBGE_5222005  \
49835                  0.0                  0.0                  0.0   

       Código_IBGE_5222054  Código_IBGE_5222203  Código_IBGE_5222302  \
49835                  0.0                  1.0                  0.0   

       Código_IBGE_5300108  
49835                  0.0  

[1 rows x 5283 columns]

In [51]:
X_new_final = X_new_encoded.drop(columns='Adjusted_funding', axis=1)

In [52]:
X_new_final.head()

Ano  Aprovação  Reprovação  Abandono  Matrículas  Docentes  \
49835  2020.0      100.0         0.0       0.0       229.0      11.0   

       Estabelecimentos  Turmas       PIB  Poverty_%  ...  \
49835               1.0     9.0  31506.97      18.05  ...   

       Código_IBGE_5221601  Código_IBGE_5221700  Código_IBGE_5221809  \
49835                  0.0                  0.0                  0.0   

       Código_IBGE_5221858  Código_IBGE_5221908  Código_IBGE_5222005  \
49835                  0.0                  0.0                  0.0   

       Código_IBGE_5222054  Código_IBGE_5222203  Código_IBGE_5222302  \
49835                  0.0                  1.0                  0.0   

       Código_IBGE_5300108  
49835                  0.0  

[1 rows x 5282 columns]

In [ ]:
#X_new = np.array(X_new).reshape(1, -1)

In [53]:
scale_features(X_new_final)

array([[0., 0., 0., ..., 0., 0., 0.]])

In [54]:
previsoes = model.predict(X_new_final)

/Users/anandxrfeu/.pyenv/versions/3.10.6/envs/schooling_resource_predicter/lib/python3.10/site-packages/sklearn/base.py:457: UserWarning: X has feature names, but RandomForestRegressor was fitted without feature names
  warnings.warn(


In [55]:
previsoes

array([3.43565209e+09])